In [1]:
from ch2.data import *
s = session('-v4')

    INFO: Using database at /home/andrew/.ch2/database.sqln


In [2]:
from ch2.squeal import *
constraint = 'Santiago'
groups = df(s.query(ActivityNearby).filter(ActivityNearby.constraint == constraint))
n_groups = len(groups.group.unique())
print(n_groups)

13


In [10]:
from bokeh.plotting import figure, output_notebook, show
from bokeh.tile_providers import CARTODBPOSITRON, STAMEN_TERRAIN, STAMEN_TONER
from bokeh.colors import RGB
import colorcet as cc
from webcolors import hex_to_rgb
from math import pi, sin, cos

side = 900
offset_a, offset_b = 400, 150
x, y = 'Spherical Mercator X', 'Spherical Mercator Y'
#palette = cc.rainbow
palette = cc.colorwheel

# labelled manually
legends = ['Farellones', 'Tobalaba', 'El Arrayan', 'San Cristobal', 'Cajon del Maipo', 'Santiago Sur', 
           'Santiago Sur 2', 'Maipu', 'Pie Andino', 'Costanera', 'Las Torres', 'Santiago Sur 3', 'Santiago Sur 4']
x_max, y_max = None, None

def p(i):
    delta = len(palette) // n_groups
    x = i / n_groups
    x = (x + 0.13 * sin(2 * pi * x))**1.2  # trying to get a perceptually well-spaced range of colours
    p = RGB(*hex_to_rgb(palette[int(x * len(palette))])).to_hsl()
    p.s = p.s * 0.9
    p.l = p.l * (0.6 + 0.5 * (i % 2))
    return p.to_rgb()
    
output_notebook()
f = figure(plot_width=side, plot_height=side, x_axis_type='mercator', y_axis_type='mercator')
for i in range(n_groups):
    source_ids = groups.loc[groups.group == i].activity_journal_id
    n_source_ids = len(source_ids)
    a = 3 * 2 * pi * i / n_groups
    dxa, dya = offset_a * sin(a), offset_a * cos(a)
    for j, source_id in enumerate(source_ids):
        b = 2 * pi * j / n_source_ids
        dxb, dyb = offset_b * sin(b), offset_b * cos(b)
        d = waypoints(s, source_id, x, y)
        f.line(x=d[x] + dxa + dxb, y=d[y] + dya + dyb, color=p(i), line_width=1.5, line_dash='dotted')
        if x_max is None:
            x_max, y_max = max(d[x]), max(d[y])
        else:
            x_max, y_max = max(x_max, max(d[x])), max(y_max, max(d[y]))
# bit of a hack to get visible lines
for i in range(n_groups):
    source_ids = groups.loc[groups.group == i].activity_journal_id
    n_source_ids = len(source_ids)
    f.line(x=[x_max, x_max*1.001], y=[y_max, y_max], color=p(i), line_width=5, line_dash='solid', 
           legend='%s (%d)' % (legends[i], n_source_ids))
f.add_tile(STAMEN_TERRAIN, alpha=0.15)
f.xaxis.axis_label = 'Longitude'
f.yaxis.axis_label = 'Latitude'
#f.x_range.range_padding = 0.25 # a little more space for the legend
show(f)

Loading BokehJS ...

In [8]:
from bokeh.plotting import figure, output_notebook, show
from bokeh.tile_providers import CARTODBPOSITRON, STAMEN_TERRAIN, STAMEN_TONER
from bokeh.colors import RGB
import colorcet as cc
from webcolors import hex_to_rgb
from math import pi, sin, cos

side = 500
offset = 40
x, y = 'Spherical Mercator X', 'Spherical Mercator Y'

source_ids = groups.loc[groups.group == 3].activity_journal_id
n_source_ids = len(source_ids)

output_notebook()
f = figure(plot_width=side, plot_height=side, x_axis_type='mercator', y_axis_type='mercator')
for i, source_id in enumerate(source_ids):
    a = 2 * pi * i / n_source_ids
    dx, dy = offset * sin(a), offset * cos(a)
    d = waypoints(s, source_id, x, y)
    f.line(x=d[x]+dx, y=d[y]+dy, color='pink', line_width=2, line_dash='solid')
f.add_tile(STAMEN_TONER, alpha=0.2)
f.xaxis.axis_label = 'Longitude'
f.yaxis.axis_label = 'Latitude'
show(f)

Loading BokehJS ...